In [1]:
from function import data_loader
import folium
import geopandas as gpd

global_path = "../data/"

# Get boundaries of London boroughs

In [2]:
# Load json
data_source = global_path + 'statistical-gis-boundaries-london/ESRI/London_Borough_Excluding_MHW.shp'
data = gpd.read_file(data_source)

# Transform cordinates
data['geometry'] = data['geometry'].to_crs(epsg=4326)
path_london_borough = global_path + "london-borough.json"
data.to_file(path_london_borough, driver="GeoJSON")

# Visualize the boroughs

In [3]:
m = folium.Map(location = [51.505453, -0.268839])
folium.GeoJson(path_london_borough).add_to(m)
m

# Add data to the map

In [4]:
# Load data
london_dic = data_loader(path=global_path, city='London')
df = london_dic['london_earnings_by_borough'].copy()
df = df[['year', 'area', 'pay']]
df['average_pay'] = df.groupby(['year', 'area'])['pay'].transform('mean')
df.drop('pay', axis=1, inplace=True)
df = df[~df['average_pay'].isna()]
df = df.drop_duplicates()
df.sort_values(by=['year', 'area'], inplace=True)
df['change_pay'] = df.groupby('area')['average_pay'].pct_change()
df = df[df['year'] == 2013]

# Plot the new map
m = folium.Map(location = [51.505453, -0.268839])
folium.Choropleth(geo_data=path_london_borough, name='choropleth', data=df, columns=['area', 'change_pay'],
                  key_on='feature.properties.NAME', fill_color='YlGn', fill_opacity=0.7, 
                  legend_name='Change in % of the average pay (before and after olympic)', 
                  line_opacity=0.2).add_to(m)
m

/home/louis/.local/lib/python3.5/site-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)
